In [50]:
import pandas as pd

columns = ['id'] +['navigateur']+ [f'action {i}' for i in range(1, 3128)]

def read_ds(ds_name: str):
    with open(f'../data/interim/{ds_name}.csv') as f:
        max_actions = max(( len( str(c).split(",")) for c in f.readlines() ))
        f.seek(0)
        _names = ["util", "navigateur"] if "train" in ds_name else ["navigateur"]
        _names.extend(range(max_actions - len(_names)))
        return pd.read_csv(f, names=_names, dtype= str)
    
df = read_ds("train")

In [51]:
pd.set_option('display.max_columns', None)
df

util      navigateur                                                  0  \
0     nuh         Firefox  Création d'un écran(infologic.core.accueil.Acc...   
1     muz   Google Chrome  Création d'un écran(infologic.core.gui.control...   
2     zrx  Microsoft Edge  Affichage d'une dialogue(infologic.core.gui.co...   
3     pou         Firefox  Création d'un écran(infologic.core.gui.control...   
4     ald   Google Chrome  Affichage d'une dialogue(infologic.acti.module...   
...   ...             ...                                                ...   
3274  muz   Google Chrome  Création d'un écran(infologic.core.gui.control...   
3275  cjr   Google Chrome  Affichage d'une dialogue(infologic.acti.module...   
3276  fuz         Firefox  Sélection d’un onglet(infologic.core.gui.contr...   
3277  cjr   Google Chrome  Création d'un écran(infologic.core.gui.control...   
3278  fwf         Firefox  Affichage d'une dialogue(infologic.orga.module...   

                                                      1  \
0                              Affichage d'une dialogue   
1     Création d'un écran(infologic.core.gui.control...   
2                                 Exécution d'un bouton   
3                                                    t5   
4                                                    t5   
...                                                 ...   
3274  Création d'un écran(infologic.core.gui.control...   
3275                              Exécution d'un bouton   
3276                   Dissimulation d'une arborescence   
3277                                                 t5   
3278                               Saisie dans un champ   

                                                      2  \
0                                 Exécution d'un bouton   
1                                                    t5   
2                                              Chainage   
3                          Exécution d'un bouton(MAINT)   
4                                 Exécution d'un bouton   
...                                                 ...   
3274                                                 t5   
3275                           Fermeture d'une dialogue   
3276                   Dissimulation d'une arborescence   
3277  Création d'un écran(infologic.core.gui.control...   
3278                              Exécution d'un bouton   

                                                      3  \
0                              Fermeture d'une dialogue   
1     Sélection d’un onglet(infologic.orga.modules.O...   
2                              Fermeture d'une dialogue   
3                              Affichage d'une dialogue   
4                              Fermeture d'une dialogue   
...                                                 ...   
3274  Sélection d’un onglet(infologic.orga.modules.O...   
3275                                                 t5   
3276                              Exécution d'un bouton   
3277                                                t10   
3278                           Fermeture d'une dialogue   

                                                      4  \
0                              Affichage d'une dialogue   
1                                                   t10   
2     Affichage d'une dialogue(infologic.acti.module...   
3                              Fermeture d'une dialogue   
4                                                   t10   
...                                                 ...   
3274                               Saisie dans un champ   
3275  Sélection d'un écran(infologic.crm.modules.CRM...   
3276                                           Chainage   
3277                          Création d'un écran(GOUV)   
3278                                                 t5   

                                                  5  \
0                             Exécution d'un bouton   
1                             Exécution d'un bouton   
2     Clic sur une grille d'historique de r

In [52]:
def filter_action(value):
    if pd.isna(value):
        return value
    for delim in [ "(", "<", "$", "1"]:
        if delim in value and (low_ind := value.index(delim)):
            value = value[:low_ind]
    return value

uniques = df.iloc[:,2:].stack().unique()
list(uniques)

["Création d'un écran(infologic.core.accueil.AccueilController)",
 "Affichage d'une dialogue",
 "Exécution d'un bouton",
 "Fermeture d'une dialogue",
 "Création d'un écran(infologic.core.gui.controllers.nested.InputFormNestedWindow)",
 't5',
 "Exécution d'un bouton(MAINT)",
 'Double-clic',
 "Lancement d'une stat(infologic.core.gui.controllers.nested.homeview.InputFormHomeView)",
 "Affichage d'un toast",
 't10',
 "Affichage d'une dialogue(MAINT)",
 't15',
 "Lancement d'une action générique",
 'Filtrage / Tri',
 "Création d'un écran",
 "Exécution d'un bouton<DEF_03/24>$JCP$",
 't20',
 "Exécution d'un bouton$JCP$",
 't25',
 "Affichage d'une dialogue$JCP$",
 'Saisie dans un champ$JCP$',
 "Fermeture d'une dialogue$JCP$",
 't30',
 't35',
 't40',
 't45',
 't50',
 't55',
 't60',
 't65',
 't70',
 't75',
 't80',
 't85',
 "Création d'un écran(infologic.acti.modules.AT_ACTIVITES.ficheactivite.ActiFicheActiviteController)",
 "Sélection d'un écran(MAINT)$JCP$",
 't90',
 't95',
 't100',
 't105',
 't1

# Feature Engineering

In [53]:
import re
import pandas as pd
import numpy as np

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.metrics import classification_report, f1_score, accuracy_score
from sklearn.svm import LinearSVC
from sklearn.linear_model import LogisticRegression
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.preprocessing import FunctionTransformer

In [54]:
train = read_ds("train")
test  = read_ds("test")

In [55]:
def row_to_sequence(row, start_col=2):
    vals = []
    for c in row.index[start_col:]:
        v = row[c]
        if pd.isna(v): break
        vals.append(str(v))
    return vals

train["seq_raw"] = train.apply(lambda r: row_to_sequence(r, start_col=2), axis=1)
test["seq_raw"]  = test.apply(lambda r: row_to_sequence(r, start_col=1), axis=1)

In [56]:
ACTION_RE = re.compile(
    r"^(?P<base>[^(<$1]+?)"              # action de base, ex: "Création d'un écran"
    r"(?:\((?P<ctrl>[^)]*)\))?"          # (controller/écran)
    r"(?:<(?P<conf>[^>]+)>)?"            # <configuration>
    r"(?:\$(?P<chain>[^$]+)\$)?"         # $chaine$
    r"(?P<edit>1)?$"                     # flag édition "1"
)

In [57]:
def normalize_token(tok: str) -> list:
    tok = tok.strip()
    if not tok: return []
    if tok.startswith("t") and tok[1:].isdigit():
        return [f"TWIN_{tok[1:]}"]  # fenêtre tXX -> token temporel

    m = ACTION_RE.match(tok)
    if not m:
        # ex. "Double-clic" simple, ou token inconnu
        return [tok.replace(" ", "_")]
    base = m.group("base").strip().replace(" ", "_")
    ctrl = (m.group("ctrl") or "").strip().replace(".", "_").replace(" ", "_")
    conf = (m.group("conf") or "").strip().replace(" ", "_")
    chain = (m.group("chain") or "").strip().replace(" ", "_")
    edit = m.group("edit")

    out = [f"A_{base}"]
    if ctrl:  out.append(f"C_{ctrl}")
    if conf:  out.append(f"CFG_{conf}")
    if chain: out.append(f"CH_{chain}")
    if edit:  out.append("EDIT_1")
    return out

def seq_to_text(seq_list):
    toks = []
    for tok in seq_list:
        toks.extend(normalize_token(tok))
    # on garde aussi quelques bigrams implicites: TF-IDF n-grammes gérera la cooccurrence
    return " ".join(toks)

train["seq_txt"] = train["seq_raw"].apply(seq_to_text)
test["seq_txt"]  = test["seq_raw"].apply(seq_to_text)

In [58]:
class SelectCols(BaseEstimator, TransformerMixin):
    def __init__(self, cols):
        self.cols = cols
    def fit(self, X, y=None): return self
    def transform(self, X):
        return X[self.cols]

class SessionStats(BaseEstimator, TransformerMixin):
    def fit(self, X, y=None): return self
    def transform(self, X):
        seqs = X["seq_raw"]
        feats = []
        for seq in seqs:
            if not isinstance(seq, list):
                feats.append([0, 0, 0])
                continue
            n_actions = sum(1 for s in seq if not (isinstance(s, str) and s.startswith("t") and s[1:].isdigit()))
            n_twins = sum(1 for s in seq if isinstance(s, str) and s.startswith("t") and s[1:].isdigit())
            unique_ctrl = len(set(re.findall(r"\((.*?)\)", " ".join(seq))))
            feats.append([n_actions, n_twins, unique_ctrl])
        return np.array(feats)

agg_feature_names = ["n_actions", "n_twins", "n_unique_ctrl"]


In [ ]:
from sklearn.preprocessing import FunctionTransformer

features_union = FeatureUnion([
    # ---- TF-IDF sur seq_txt (1D string array) ----
    ("tfidf", Pipeline([
        ("sel_txt", SelectCols(["seq_txt"])),
        ("to_1d", FunctionTransformer(lambda df: df["seq_txt"].astype(str).tolist(), validate=False)),
        ("tfidf", TfidfVectorizer(
            min_df=3,
            ngram_range=(1,1),
            max_features=20000,
            sublinear_tf=True,
            strip_accents="unicode"
        ))
    ])),
    # ---- One-hot navigateur (2D array) ----
    ("nav", Pipeline([
        ("sel_nav", SelectCols(["navigateur"])),
        ("to_2d", FunctionTransformer(lambda df: df.values, validate=False)),
        ("ohe", OneHotEncoder(handle_unknown="ignore", sparse_output=True))
    ])),
    # ---- Stats agrégées (inchangé) ----
    ("agg", Pipeline([
        ("sel_raw", SelectCols(["seq_raw"])),
        ("stats", SessionStats()),
        ("to_df", FunctionTransformer(lambda a: pd.DataFrame(
            a, columns=["n_actions","n_twins","n_unique_ctrl"]), validate=False))
    ]))
], n_jobs=-1)


# Training a linear model : Support Vector Machine Classifier

In [60]:
clf = LinearSVC(C=5.0)  

pipe = Pipeline([
    ("features", features_union),
    ("clf", clf),
])


X = train[["seq_raw","seq_txt","navigateur"]].copy()
y = train["util"].astype(str)

X_tr, X_va, y_tr, y_va = train_test_split(
    X, y, test_size=0.2, random_state=42, stratify=y
)

pipe.fit(X_tr, y_tr)
pred = pipe.predict(X_va)
print("Accuracy:", accuracy_score(y_va, pred))
print("F1-score:", f1_score(y_va, pred, average="weighted"))
print(classification_report(y_va, pred, digits=3))

Accuracy: 0.9024390243902439
F1-score: 0.8916036600097039
              precision    recall  f1-score   support

         aho      1.000     0.500     0.667         2
         ajo      1.000     0.333     0.500         3
         akx      0.500     0.667     0.571         3
         ald      1.000     0.667     0.800         3
         ats      1.000     1.000     1.000         2
         avt      1.000     0.667     0.800         3
         azn      1.000     1.000     1.000         1
         azo      1.000     0.500     0.667         2
         azx      0.667     1.000     0.800         2
         bez      0.500     1.000     0.667         1
         bfg      1.000     1.000     1.000         3
         bgn      0.833     1.000     0.909         5
         blf      1.000     1.000     1.000         2
         bos      0.000     0.000     0.000         2
         bou      1.000     1.000     1.000         2
         btl      1.000     1.000     1.000         3
         byo      0.750

/Users/anasselmonta/Documents/S9 MOD/Data Science/BEs/BEsVenv/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/anasselmonta/Documents/S9 MOD/Data Science/BEs/BEsVenv/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/anasselmonta/Documents/S9 MOD/Data Science/BEs/BEsVenv/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` paramete

In [65]:
pipe.named_steps['features'].transform(X)

<3279x2361 sparse matrix of type '<class 'numpy.float64'>'
	with 645015 stored elements in Compressed Sparse Row format>

In [ ]:
import pandas as pd
import plotly.express as px
import umap.umap_ as umap
from sklearn.preprocessing import StandardScaler

X_umap = pipe.named_steps['features'].transform(X).toarray()
# 1️⃣ Standardisation des features
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X_umap)

# 2️⃣ UMAP en 2D
reducer = umap.UMAP(
    n_neighbors=20,
    min_dist=0.0,
    n_components=2,
    random_state=42
)
embedding = reducer.fit_transform(X_scaled)

# 3️⃣ Construction du DataFrame pour plotly
umap_df = pd.DataFrame(embedding, columns=['UMAP1', 'UMAP2'])
umap_df['Classe'] = y.values

# 4️⃣ Visualisation interactive
fig = px.scatter(
    umap_df,
    x='UMAP1',
    y='UMAP2',
    color='Classe',
    title='Projection UMAP 2D',
    color_discrete_sequence=px.colors.qualitative.Set1,
    hover_data=umap_df.columns
)
fig.update_traces(marker=dict(size=6, line=dict(width=0.5, color='DarkSlateGrey')))
fig.update_layout(template='plotly_white', legend_title_text='Classe')
fig.show()

/Users/anasselmonta/Documents/S9 MOD/Data Science/BEs/BEsVenv/lib/python3.9/site-packages/umap/umap_.py:1952: UserWarning:

n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.



# Prediction on test set and submission

In [ ]:
pipe.fit(X, y)

test_df = test[["seq_raw","seq_txt","navigateur"]].copy()
test_pred = pipe.predict(test_df)

sub = pd.DataFrame({
    "RowId": np.arange(len(test_pred)),
    "prediction": test_pred
})


In [27]:
sub

row_id util
0         0  hzx
1         1  prb
2         2  jmq
3         3  psg
4         4  cvw
..      ...  ...
319     319  eqw
320     320  usg
321     321  cjr
322     322  fuy
323     323  fxg

[324 rows x 2 columns]

In [32]:
sub.columns = [['RowId', 'prediction']]
sub['RowId'] = sub['RowId'] + 1

In [33]:
sub

RowId prediction
0       1        hzx
1       2        prb
2       3        jmq
3       4        psg
4       5        cvw
..    ...        ...
319   320        eqw
320   321        usg
321   322        cjr
322   323        fuy
323   324        fxg

[324 rows x 2 columns]

In [34]:
sub.to_csv("../submissions/submission_v0.csv", index=False)
print("Saved submission.csv")

Saved submission.csv


In [37]:
print("F1-score:", f1_score(y_va, pred, average="weighted"))

F1-score: 0.8916036600097039
